##### Copyright 2020 The TensorFlow Authors.

In [1]:
#@title Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
#
# https://www.apache.org/licenses/LICENSE-2.0
#
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.

# Model Averaging

<table class="tfo-notebook-buttons" align="left">
  <td>
    <a target="_blank" href="https://www.tensorflow.org/addons/tutorials/average_optimizers_callback"><img src="https://www.tensorflow.org/images/tf_logo_32px.png" />View on TensorFlow.org</a>
  </td>
  <td>
    <a target="_blank" href="https://colab.research.google.com/github/tensorflow/addons/blob/master/docs/tutorials/average_optimizers_callback.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png" />Run in Google Colab</a>
  </td>
  <td>
    <a target="_blank" href="https://github.com/tensorflow/addons/blob/master/docs/tutorials/average_optimizers_callback.ipynb"><img src="https://www.tensorflow.org/images/GitHub-Mark-32px.png" />View source on GitHub</a>
  </td>
      <td>
    <a href="https://storage.googleapis.com/tensorflow_docs/addons/docs/tutorials/average_optimizers_callback.ipynb"><img src="https://www.tensorflow.org/images/download_logo_32px.png" />Download notebook</a>
  </td>
</table>


## Overview

This notebook demonstrates how to use Moving Average Optimizer along with the Model Average Checkpoint from tensorflow addons package.


## Moving Averaging 

> The advantage of Moving Averaging is that they are less prone to rampant loss shifts or irregular data representation in the latest batch. It gives a smooothened and a more general idea of the model training until some point.

## Stochastic Averaging

> Stochastic Weight Averaging converges to wider optima. By doing so, it resembles geometric ensembeling. SWA is a simple method to improve model performance when used as a wrapper around other optimizers and averaging results from different points of trajectory of the inner optimizer.

## Model Average Checkpoint 

> `callbacks.ModelCheckpoint` doesn't give you the option to save moving average weights in the middle of training, which is why Model Average Optimizers required a custom callback. Using the ```update_weights``` parameter, ```ModelAverageCheckpoint``` allows you to:
1.   Assign the moving average weights to the model, and save them.
2.   Keep the old non-averaged weights, but the saved model uses the average weights.

## Setup

In [2]:
!pip install -U tensorflow-addons

  Using cached tensorflow_addons-0.17.1-cp39-cp39-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (1.1 MB)


  Using cached typeguard-2.13.3-py3-none-any.whl (17 kB)


In [3]:
import tensorflow as tf
import tensorflow_addons as tfa

In [4]:
import numpy as np
import os

## Build Model 

In [5]:
def create_model(opt):
    model = tf.keras.models.Sequential([
        tf.keras.layers.Flatten(),                         
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(64, activation='relu'),
        tf.keras.layers.Dense(10, activation='softmax')
    ])

    model.compile(optimizer=opt,
                    loss='sparse_categorical_crossentropy',
                    metrics=['accuracy'])

    return model

## Prepare Dataset

In [6]:
#Load Fashion MNIST dataset
train, test = tf.keras.datasets.fashion_mnist.load_data()

images, labels = train
images = images/255.0
labels = labels.astype(np.int32)

fmnist_train_ds = tf.data.Dataset.from_tensor_slices((images, labels))
fmnist_train_ds = fmnist_train_ds.shuffle(5000).batch(32)

test_images, test_labels = test

 8192/29515 [=======>......................] - ETA: 0s

29515/29515 [==============================] - 0s 0us/step


    8192/26421880 [..............................] - ETA: 0s

11182080/26421880 [===========>..................] - ETA: 0s

26421880/26421880 [==============================] - 0s 0us/step


5148/5148 [==============================] - 0s 0us/step


   8192/4422102 [..............................] - ETA: 0s

4422102/4422102 [==============================] - 0s 0us/step


We will be comparing three optimizers here:

*   Unwrapped SGD
*   SGD with Moving Average
*   SGD with Stochastic Weight Averaging

And see how they perform with the same model.

In [7]:
#Optimizers 
sgd = tf.keras.optimizers.SGD(0.01)
moving_avg_sgd = tfa.optimizers.MovingAverage(sgd)
stocastic_avg_sgd = tfa.optimizers.SWA(sgd)

Both ```MovingAverage``` and ```StochasticAverage``` optimizers use ```ModelAverageCheckpoint```.

In [8]:
#Callback 
checkpoint_path = "./training/cp-{epoch:04d}.ckpt"
checkpoint_dir = os.path.dirname(checkpoint_path)

cp_callback = tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_dir,
                                                 save_weights_only=True,
                                                 verbose=1)
avg_callback = tfa.callbacks.AverageModelCheckpoint(filepath=checkpoint_dir, 
                                                    update_weights=True)

## Train Model


### Vanilla SGD Optimizer 

In [9]:
#Build Model
model = create_model(sgd)

#Train the network
model.fit(fmnist_train_ds, epochs=5, callbacks=[cp_callback])

Epoch 1/5


   1/1875 [..............................] - ETA: 18:04 - loss: 2.2988 - accuracy: 0.0938

  26/1875 [..............................] - ETA: 3s - loss: 2.1848 - accuracy: 0.1671   

  51/1875 [..............................] - ETA: 3s - loss: 2.0870 - accuracy: 0.2855

  76/1875 [>.............................] - ETA: 3s - loss: 1.9848 - accuracy: 0.3536

...

1817/1875 [============================>.] - ETA: 0s - loss: 0.4128 - accuracy: 0.8556

1844/1875 [============================>.] - ETA: 0s - loss: 0.4124 - accuracy: 0.8557

1872/1875 [============================>.] - ETA: 0s - loss: 0.4126 - accuracy: 0.8556


Epoch 5: saving model to ./training


1875/1875 [==============================] - 4s 2ms/step - loss: 0.4127 - accuracy: 0.8556


In [10]:
#Evalute results
model.load_weights(checkpoint_dir)
loss, accuracy = model.evaluate(test_images, test_labels, batch_size=32, verbose=2)
print("Loss :", loss)
print("Accuracy :", accuracy)

313/313 - 1s - loss: 76.6787 - accuracy: 0.8127 - 531ms/epoch - 2ms/step


Loss : 76.67872619628906
Accuracy : 0.8126999735832214


### Moving Average SGD

In [11]:
#Build Model
model = create_model(moving_avg_sgd)

#Train the network
model.fit(fmnist_train_ds, epochs=5, callbacks=[avg_callback])

Epoch 1/5


   1/1875 [..............................] - ETA: 14:08 - loss: 2.3055 - accuracy: 0.1250

  25/1875 [..............................] - ETA: 4s - loss: 2.2074 - accuracy: 0.2250   

  49/1875 [..............................] - ETA: 3s - loss: 2.1127 - accuracy: 0.3144

  73/1875 [>.............................] - ETA: 3s - loss: 2.0253 - accuracy: 0.3763

...

1802/1875 [===========================>..] - ETA: 0s - loss: 0.4139 - accuracy: 0.8552

1828/1875 [============================>.] - ETA: 0s - loss: 0.4133 - accuracy: 0.8551

1853/1875 [============================>.] - ETA: 0s - loss: 0.4128 - accuracy: 0.8553

INFO:tensorflow:Assets written to: ./training/assets


1875/1875 [==============================] - 4s 2ms/step - loss: 0.4133 - accuracy: 0.8550


In [12]:
#Evalute results
model.load_weights(checkpoint_dir)
loss, accuracy = model.evaluate(test_images, test_labels, batch_size=32, verbose=2)
print("Loss :", loss)
print("Accuracy :", accuracy)

313/313 - 1s - loss: 76.6787 - accuracy: 0.8127 - 532ms/epoch - 2ms/step


Loss : 76.67872619628906
Accuracy : 0.8126999735832214


### Stocastic Weight Average SGD 

In [13]:
#Build Model
model = create_model(stocastic_avg_sgd)

#Train the network
model.fit(fmnist_train_ds, epochs=5, callbacks=[avg_callback])

Epoch 1/5


   1/1875 [..............................] - ETA: 27:03 - loss: 2.4404 - accuracy: 0.1250

  20/1875 [..............................] - ETA: 5s - loss: 2.2758 - accuracy: 0.1047   

  40/1875 [..............................] - ETA: 4s - loss: 2.1817 - accuracy: 0.1586

  60/1875 [..............................] - ETA: 4s - loss: 2.0945 - accuracy: 0.2417

...

1822/1875 [============================>.] - ETA: 0s - loss: 0.5077 - accuracy: 0.8239

1842/1875 [============================>.] - ETA: 0s - loss: 0.5076 - accuracy: 0.8238

1863/1875 [============================>.] - ETA: 0s - loss: 0.5070 - accuracy: 0.8239

INFO:tensorflow:Assets written to: ./training/assets


1875/1875 [==============================] - 5s 3ms/step - loss: 0.5066 - accuracy: 0.8241


In [14]:
#Evalute results
model.load_weights(checkpoint_dir)
loss, accuracy = model.evaluate(test_images, test_labels, batch_size=32, verbose=2)
print("Loss :", loss)
print("Accuracy :", accuracy)

313/313 - 1s - loss: 76.6787 - accuracy: 0.8127 - 504ms/epoch - 2ms/step


Loss : 76.67872619628906
Accuracy : 0.8126999735832214
